
_____________________________________________________________
# LP-DAAC's OPERA DIST-ALERT-HLS Methodology

The OPERA Land Surface Disturbance Alert from Harmonized Landsat Sentinel-2 (HLS) product Version 1 utilizes data from Landsat 8, Landsat 9, Sentinel-2A, and Sentinel-2B to map vegetation disturbance alerts at 30-meter spatial resolution. These alerts signify decreased vegetation cover within HLS pixels, offering insight into disturbance trends and auxiliary disturbance information. The data, provided in Cloud Optimized GeoTIFF format, consists of 19 layers, including disturbance status, loss or anomaly, maximum loss anomaly, disturbance confidence, date of disturbance, count of observations with loss anomalies, days of ongoing anomalies, and day of last disturbance detection, among others. This comprehensive dataset enhances sensitivity to land changes, providing valuable information on both large magnitude/short duration and small magnitude/long duration disturbances.

In [1]:
# Standard library imports
import os
import sys
import warnings
from datetime import datetime
from getpass import getpass
from netrc import netrc
from platform import system
from subprocess import Popen

# Third-party library imports
import numpy as np
import pandas as pd
import geopandas as gpd
import hvplot.xarray
import rioxarray
import xarray as xr
from bokeh.models import FixedTicker
from bokeh.plotting import show
from folium import plugins
from holoviews import opts
from IPython.display import display
from osgeo import gdal
from rioxarray.merge import merge_arrays
from shapely.geometry import box, shape
import panel as pn

import cartopy.crs as ccrs
import cartopy.feature as cfeature
import folium
import geoviews as gv
import holoviews as hv
from holoviews.operation.datashader import rasterize
import matplotlib.pyplot as plt

from holoviews.plotting.util import process_cmap
from bokeh.io.export import export_png
from bokeh.io import output_notebook, show
from bokeh.models import FixedTicker
from bokeh.plotting import figure
from bokeh.models import HoverTool

# Earth data access and STAC client
import earthaccess
from pystac_client import Client  

# Custom utility functions
from modules.stack_bands import stack_bands
from modules.dist_utils import (
    intersection_percent, time_and_area_cube,
    compute_area, standard_date, colorize, mask_rasters,
    getbasemaps, transform_data_for_folium)
from modules.dist_triplot import VegDistVisualizer
from modules.test import VegDistVisualize

# Initialize Holoviews and Geoviews extensions
hv.extension('bokeh')
gv.extension('bokeh', 'matplotlib')

# Suppress warnings
warnings.filterwarnings('ignore')


Loading BokehJS ...

Loading BokehJS ...

### Product Background
---

The DIST product maps per pixel vegetation disturbance (specifically, vegetation cover loss) from the Harmonized Landsat-8 and Sentinel-2 A/B (HLS) scenes. Vegetation disturbance is mapped when there is an indicated decrease in vegetation cover within an HLS pixel. This notebook focuses on relevant layers within the **DIST_ALERT** product for wildfire applications, which is released at the cadence of HLS imagery. 

In [24]:
# Set the current working directory to a variable
project_root = os.getcwd()

# Change the current working directory to the directory stored in inDir
os.chdir(project_root)
output_dir = os.path.join(project_root, 'OPERA_Exports')

# Login to earthaccess, persisting the session
earthaccess.login(persist=True)

In [9]:
# GDAL configurations used to successfully access PODAAC Cloud Assets via vsicurl 
gdal.SetConfigOption('GDAL_HTTP_COOKIEFILE','~/cookies.txt')
gdal.SetConfigOption('GDAL_HTTP_COOKIEJAR', '~/cookies.txt')
gdal.SetConfigOption('GDAL_DISABLE_READDIR_ON_OPEN','EMPTY_DIR')
gdal.SetConfigOption('CPL_VSIL_CURL_ALLOWED_EXTENSIONS','TIF, TIFF')

In [10]:
# User-Defined Parameters

# Define the area of interest (AOI) as a bounding box with coordinates
aoi = box(-121.704682, 34.918007, -119.874127,  36.399885)

# Define the start date for the search period
start_date = datetime(2023, 1, 1)

# Define the stop date for the search period (uncomment the dynamic stop date line if needed)
# stop_date = f"{datetime.today().strftime('%Y-%m-%d')} 23:59:59"
stop_date = datetime(2023, 3, 30)

# Set the threshold for overlap percentage
overlap_threshold = 20

# Set the threshold for cloud cover percentage
cloud_cover_threshold = 20

# Print the search parameters
print(f"Search between {start_date} and {stop_date}")
print(f"With AOI: {aoi.__geo_interface__}")


Search between 2023-01-01 00:00:00 and 2023-03-30 00:00:00
With AOI: {'type': 'Polygon', 'coordinates': (((-119.874127, 34.918007), (-119.874127, 36.399885), (-121.704682, 36.399885), (-121.704682, 34.918007), (-119.874127, 34.918007)),)}


In [11]:


# Define the CMR-STAC API Endpoint
stac = 'https://cmr.earthdata.nasa.gov/cloudstac/'

# Open the STAC API client for the specified endpoint and collection
api = Client.open(f'{stac}/LPCLOUD/')
collections = ['OPERA_L3_DIST-ALERT-HLS_V1']

# Define the search parameters
search_params = {
    "collections": collections,             # List of collections to search within
    "intersects": aoi.__geo_interface__,    # Area of interest (AOI) in GeoJSON format
    "datetime": [start_date, stop_date],    # Time range for the search
    "limit": 50,                            # Maximum number of items per request
    "max_items": 1000                       # Maximum number of items to return
}

# Perform the search using the specified parameters
search_dist = api.search(**search_params)

# Count the number of items found
items = list(search_dist.get_items())
num_items = len(items)

# Print the number of items found
print(f"Number of images found: {num_items}")


Number of images found: 203


In [12]:
# Filter datasets based on spatial overlap and cloud cover

# Define the AOI geometry in GeoJSON format
intersects_geometry = aoi.__geo_interface__

# Print percent overlap values before filtering
print("Percent overlap before filtering: ")
print([f"{intersection_percent(i, intersects_geometry):.2f}" for i in search_dist.items()])

# Print percent cloud cover values before filtering
print("\nPercent cloud cover before filtering: ")
print([f"{i.properties['eo:cloud_cover']}" for i in search_dist.items()])


Percent overlap before filtering: 
['6.56', '12.44', '10.45', '15.97', '33.47', '33.96', '4.36', '10.12', '11.51', '8.75', '6.56', '28.91', '4.36', '15.97', '1.33', '0.82', '10.07', '3.04', '2.64', '13.73', '11.54', '5.69', '37.28', '5.80', '24.64', '0.16', '7.09', '11.50', '8.81', '6.56', '29.06', '4.36', '15.97', '1.38', '0.88', '10.09', '3.04', '2.64', '13.73', '11.80', '5.95', '37.28', '6.02', '25.36', '11.50', '8.81', '6.56', '29.05', '4.36', '15.97', '10.09', '3.53', '3.70', '0.34', '9.84', '14.16', '4.36', '6.96', '6.56', '12.44', '10.49', '15.97', '33.47', '34.06', '4.36', '10.12', '11.51', '3.41', '3.45', '13.73', '12.02', '6.16', '3.83', '26.07', '0.44', '35.79', '8.54', '8.45', '6.56', '28.12', '4.36', '15.97', '1.09', '9.96', '0.51', '2.04', '13.71', '32.53', '8.24', '6.56', '12.44', '10.52', '15.97', '33.47', '34.12', '4.36', '10.12', '11.51', '3.37', '3.36', '13.73', '6.19', '12.05', '26.17', '6.26', '0.50', '37.28', '8.64', '11.50', '6.56', '12.44', '10.67', '15.97', '33

In [14]:
# Apply spatial overlap and cloud cover threshold

dist_filtered = (
    i for i in search_dist.items() if (intersection_percent(i, intersects_geometry) 
                                       > overlap_threshold and 
                                       i.properties['eo:cloud_cover'] < cloud_cover_threshold))

# Convert the filtered datasets generator to a list
dist_data = list(dist_filtered)

# Convert the first dataset in the list to a dictionary format
first_dataset_dict = dist_data[0].to_dict()

# Print the dictionary representation of the first dataset
first_dataset_dict


{'type': 'Feature',
 'stac_version': '1.0.0',
 'id': 'OPERA_L3_DIST-ALERT-HLS_T10SGE_20230201T183435Z_20231220T210944Z_L9_30_v1',
 'properties': {'eo:cloud_cover': 2,
  'datetime': '2023-02-01T18:34:35.471000Z',
  'start_datetime': '2023-02-01T18:34:35.471Z',
  'end_datetime': '2023-02-01T18:34:59.358Z'},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[-119.6016716, 35.1072182],
    [-119.5595813, 36.095467],
    [-120.5312329, 36.119179],
    [-120.80132, 35.1349383],
    [-119.6016716, 35.1072182]]]},
 'links': [{'rel': 'self',
   'href': 'https://cmr.earthdata.nasa.gov/cloudstac/LPCLOUD/collections/OPERA_L3_DIST-ALERT-HLS_V1.v1/items/OPERA_L3_DIST-ALERT-HLS_T10SGE_20230201T183435Z_20231220T210944Z_L9_30_v1'},
  {'rel': 'parent',
   'href': 'https://cmr.earthdata.nasa.gov/cloudstac/LPCLOUD/collections/OPERA_L3_DIST-ALERT-HLS_V1.v1'},
  {'rel': 'collection',
   'href': 'https://cmr.earthdata.nasa.gov/cloudstac/LPCLOUD/collections/OPERA_L3_DIST-ALERT-HLS_V1.v1'},
  {'rel': 'root',

In [15]:
# Print search information

# Total granules after applying the search filter
print(f"Total granules after search filter: {len(dist_data)}")

# Print percent overlap values for each filtered granule
print("Percent-overlap: ")
print([f"{intersection_percent(i, intersects_geometry):.2f}" for i in dist_data])

# Print cloud cover values for each filtered granule
print("Cloud-cover: ")
print([f"{x.properties['eo:cloud_cover']}" for x in dist_data])


Total granules after search filter: 9
Percent-overlap: 
['28.91', '37.28', '24.64', '29.06', '33.47', '34.12', '32.52', '33.47', '34.28']
Cloud-cover: 
['2', '0', '0', '0', '3', '16', '1', '8', '7']


In [16]:
# Create table of search results

# Initialize an empty list to hold the search result data
dist_data_df = []

# Iterate through each item in the filtered dataset list
for item in dist_data:
    item.to_dict()  # Convert the item to a dictionary (optional, for debugging)
    
    # Extract information from the item
    fn = item.id.split('_')
    ID = fn[3]                           # Extract Tile ID
    sensor = fn[6]                       # Extract Sensor information
    dat = item.datetime.strftime('%Y-%m-%d')  # Extract and format the date
    spatial_coverage = intersection_percent(item, intersects_geometry)  # Calculate spatial coverage
    cloud_cover = item.properties['eo:cloud_cover']  # Extract cloud cover percentage
    geom = item.geometry                 # Extract geometry
    bbox = item.bbox                     # Extract bounding box
    
    # Extract the href information for all bands
    band_links = [item.assets[links].href for links in item.assets.keys()]
    
    # Append the extracted information as a row in the list
    dist_data_df.append([ID, sensor, dat, geom, bbox, spatial_coverage, cloud_cover, band_links])

# Convert the list to a DataFrame with specified column names
dist_data_df = pd.DataFrame(dist_data_df, columns=['TileID', 'Sensor', 'Date', 'Coords', 'bbox', 'SpatialCoverage', 'CloudCover', 'BandLinks'])

# Display the DataFrame
dist_data_df

TileID Sensor        Date  \
0  T10SGE     L9  2023-02-01   
1  T10SFE     L9  2023-02-08   
2  T10SGE     L9  2023-02-08   
3  T10SGE     L8  2023-02-09   
4  T10SGE    S2B  2023-03-02   
5  T10SFE    S2A  2023-03-07   
6  T10SFE    S2B  2023-03-25   
7  T10SGE    S2A  2023-03-27   
8  T10SFE    S2A  2023-03-27   

                                              Coords  \
0  {'type': 'Polygon', 'coordinates': [[[-119.601...   
1  {'type': 'Polygon', 'coordinates': [[[-120.697...   
2  {'type': 'Polygon', 'coordinates': [[[-120.264...   
3  {'type': 'Polygon', 'coordinates': [[[-119.601...   
4  {'type': 'Polygon', 'coordinates': [[[-119.601...   
5  {'type': 'Polygon', 'coordinates': [[[-120.697...   
6  {'type': 'Polygon', 'coordinates': [[[-120.969...   
7  {'type': 'Polygon', 'coordinates': [[[-119.601...   
8  {'type': 'Polygon', 'coordinates': [[[-120.697...   

                                               bbox  SpatialCoverage  \
0   [-120.80132, 35.107218, -119.559581, 36.119179]        28.913674   
1  [-121.902146, 35.133006, -120.668785, 36.139741]        37.276231   
2   [-120.805269, 35.124003, -119.96787, 36.124284]        24.636495   
3  [-120.805269, 35.107218, -119.559581, 36.119525]        29.058243   
4  [-120.805269, 35.107218, -119.559581, 36.124284]        33.474094   
5  [-121.761539, 35.133006, -120.668785, 36.135326]        34.124789   
6  [-121.902146, 35.137874, -120.668785, 36.139741]        32.523393   
7  [-120.805269, 35.107218, -119.559581, 36.124284]        33.474094   
8  [-121.766149, 35.133006, -120.668785, 36.135398]        34.275311   

   CloudCover                                          BandLinks  
0           2  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
1           0  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
2           0  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
3           0  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
4           3  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
5          16  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
6           1  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
7           8  [https://data.lpdaac.earthdatacloud.nasa.gov/l...  
8           7  [https://data.lpdaac.earthdatacloud.nasa.gov/l...

In [17]:
# Extract a specific dataset from dist_data and convert it to a dictionary
choice_dataset_dict = dist_data[4].to_dict()

# Define the STAC item using the dataset dictionary
stac_item = choice_dataset_dict

# Define the list of bands to stack
bandlist = ['VEG-ANOM-MAX', 'VEG-DIST-DATE', 'VEG-DIST-STATUS']


In [18]:
# Stack the bands
da, crs = stack_bands(stac_item, bandlist)

# Print the stacked bands dataset and CRS
print(da)
print("CRS:", crs)

<xarray.Dataset> Size: 80MB
Dimensions:      (longitude: 3660, latitude: 3660, band: 3)
Coordinates:
  * longitude    (longitude) float64 29kB 7e+05 7e+05 ... 8.097e+05 8.097e+05
  * latitude     (latitude) float64 29kB 4e+06 4e+06 4e+06 ... 3.89e+06 3.89e+06
    spatial_ref  int32 4B 0
  * band         (band) int32 12B 1 2 3
Data variables:
    z            (band, latitude, longitude) int16 80MB 0 0 0 0 0 ... 0 0 0 0 0
CRS: EPSG:32610


In [19]:
# Exhibit the three disturbance plots


# Instantiate the visualizer with the dataset
visualizer = VegDistVisualizer(da)

# Create and serve the layout
layout = visualizer.panel_layout()
layout.servable()

Column
    [0] Row(sizing_mode='scale_width')
        [0] DateSlider(end=Timestamp('2023-03-02 0..., name='Min Date', sizing_mode='stretch_width', start=Timestamp('2020-12-31 0..., value=Timestamp('2020-12-31 0...)
        [1] DateSlider(end=Timestamp('2023-03-02 0..., name='Max Date', sizing_mode='stretch_width', start=Timestamp('2020-12-31 0..., value=Timestamp('2023-03-02 0...)
    [1] Row
        [0] ParamMethod(method, _pane=HoloViews, defer_load=False, sizing_mode='scale_width')
        [1] ParamMethod(method, _pane=HoloViews, defer_load=False, sizing_mode='scale_width')
        [2] ParamMethod(method, _pane=HoloViews, defer_load=False, sizing_mode='scale_width')

In [25]:
# Ensure that Bokeh and HoloViews output works in the notebook
output_notebook()
pn.extension()

# Assume the data array 'da' is already defined and loaded

# Define specific start and end dates for filtering
specific_start_date = pd.Timestamp('2023-01-01')
specific_end_date = pd.Timestamp('2023-01-25')

# Calculate the number of days since the start_date for these specific dates
min_days_specific = (specific_start_date - pd.Timestamp('2020-12-31')).days
max_days_specific = (specific_end_date - pd.Timestamp('2020-12-31')).days

# Filter Band 2 data array based on the specific dates
masked_band2 = da.z.sel(band=2).where(
    (da.z.sel(band=2) >= min_days_specific) & (da.z.sel(band=2) <= max_days_specific), np.nan
)

# Mask Band 3 data using the filtered Band 2
masked_band3 = da.z.sel(band=3).where(
    (masked_band2.notnull()) & (da.z.sel(band=3) != 0) & (da.z.sel(band=3) != 255), np.nan
)

# Define a portable output directory
output_dir = os.path.join(project_root, 'OPERA_Exports')
os.makedirs(output_dir, exist_ok=True)  # Create the directory if it doesn't exist

# Save the masked_band3 data to a GeoTIFF file in the portable output directory
output_file = os.path.join(output_dir, "Veg_dist_test.tif")
masked_band3.rio.to_raster(output_file)

# Set up the base map
base = gv.tile_sources.EsriImagery.opts(width=1000, height=1000, padding=0.1)

# Generate the plot
plot = masked_band3.hvplot.image(
    x='longitude', 
    y='latitude', 
    crs=ccrs.PlateCarree(), 
    rasterize=True, 
    dynamic=False,  # Disable dynamic features
    aspect='equal', 
    frame_width=700, 
    frame_height=700, 
    cmap='hot_r', 
    alpha=0.8
).opts(
    title="VEG_DIST (Specific Dates)", 
    clim=(0, 4), 
    colorbar_opts={
        'title': 'VEG_DIST',
        'ticker': FixedTicker(ticks=[0, 1, 2, 3, 4]),
        'title_standoff': 10,
        'label_standoff': 8,
        'major_label_text_font_size': '10pt',
        'title_text_font_size': '12pt'
    }, 
    xlabel='Longitude', 
    ylabel='Latitude'
) * base

# Render the plot using Holoviews
bokeh_plot = hv.render(plot)

# Set explicit width and height for the Bokeh plot
bokeh_plot.width = 600
bokeh_plot.height = 800

# Display the plot in the notebook
show(bokeh_plot)

print(f"GeoTIFF file saved at: {output_file}")


Loading BokehJS ...

GeoTIFF file saved at: C:\Users\skcor\Github\EA_FinalProj\OPERA_Exports\Veg_dist_test.tif
